# Кузин М.А. гр. 4.6

**Цель работы**

Реализовать генетический алгоритм для нахождения минимума функции.

**Ход работы**

*Импорт библиотек*

In [1]:
import matplotlib.pyplot as plt
from matplotlib import cm
import matplotlib
matplotlib.rcParams['animation.embed_limit'] = 2**128

import numpy as np
import random
import math
# Enable interactive plot
# %matplotlib notebook
from matplotlib.animation import FuncAnimation, FFMpegWriter
from IPython.display import HTML
from collections import defaultdict

*Функция, у которой мы ищем минимум:*

37. $f(x, y) = /dfrac{1}{|x|+ 4} + /dfrac{3}{y2+ 4}$

In [2]:
def my_func(x):
    return 1/(abs(x[0]) + 4) + 3/(x[1]**2+4)

Нужно сделать класс, на вход принимающий некую функцию и параметры:
- область определения
- объем поколения
- кол-во смены поколений (итераций)
- вероятность мутации для отдельного гена
- выбор из двух видов мутаций (рандом и мат ожидание)
- выбор способа селекции (по-умолчанию д)
- в качестве похожести Евклидова метрика (torch.cdist(population, population, p=2, compute_mode="donot_use_mm_for_euclid_dist"))
Можно для отдельной хромосомы через torch.dist(a, b)

Метод рулетки - Softmax
Вывод наилучшая точка + значение функции

In [3]:
from dataclasses import field, fields, dataclass
from typing import Callable, DefaultDict
from copy import deepcopy


@dataclass
class Genom2000:

    population_size: int = 100
    target_func: Callable = my_func
    shape_graph: tuple[int] = (-20, 20, 0.25)
    max_epoch: int = 100
    prob_mutation: float = 0.05
    selection_type: str = field(default='рулетки') # турнир/рулетки/ранжирования/равномерное ранжирования
                                                  # сигма отсечение
    mutation_type: str = field(default="не совсем рандом") # рандом/не рандом
    sigma: float = field(default=5)
    a: float = field(default=1.5) #a in [1, 2]
    choice_parent_type: str = field(default="панксимия") # панксимия/аутбридинг/инбридинг

    optim_point: list = field(init=False, default=None)
    X: list = field(init=False, default=None)
    Y: list = field(init=False, default=None)
    Z: list = field(init=False, default=None)

    selection_types: DefaultDict = field(
        init=False,
        default_factory=lambda: defaultdict(
            lambda: "e", {
                "турнир":"a",
                "рулетки":"b",
                "ранжирования":"c",
                "равномерное ранжирования":"d"
                }
            )
        )


    # Турнир
    def selection_a(self, x: np.array) -> list:
        x_n = x.tolist()
        random.shuffle(x_n)
        for _ in range(int(len(x)/2)):
            parent_1 = x_n.pop(0)
            parent_2 = x_n.pop(0)
            x_n.append(parent_1 if parent_1[2] < parent_2[2] else parent_2)
        return x_n


    # Метод рулетки
    def selection_b(self, x: np.array) -> list:
        x_n = np.column_stack((x, x[:,2]/sum(x[:,2])))
        x_n = x_n[x_n[:,3].argsort()][:,:3]
        return x_n.tolist()[:self.len_selection]


    # Метод ранжирования
    def selection_с(self, x: np.array) -> list:
        a = self.a if self.a >=1 and self.a <= 2 else 1
        b = 2 - self.a
        n = len(x)

        x_n = x[x[:,2].argsort()][::-1]
        x_n = np.column_stack((x_n, [1/n*(a - (a - b)*(i-1)/(n-1)) for i in range(n)]))
        x_n = x_n[x_n[:,3].argsort()][:,:3]
        return x_n.tolist()[:self.len_selection]


    # Равномерное ранжирование
    def selection_d(self, x: np.array) -> list:
        return sorted(x.tolist(), key=lambda x: x[2])[:self.len_selection]


    # Сигма-отсечение
    def selection_e(self, x: np.array) -> list:
        f = 1 + (x[:,2]-x[:,2].mean())/(2*x[:,2].std())
        x_n = np.column_stack((x, f/sum(f)))
        x_n = x_n[x_n[:,3].argsort()][:,:3]
        return x_n.tolist()[:self.len_selection]


    # Создание начальной популяции
    def create_population(self) -> None:
        new_population = []
        while len(new_population) < self.population_size:
            x = [random.uniform(-20, 20), random.uniform(-20, 20)]
            x.append(self.target_func([x[0], x[1]]))
            if new_population.count(x) == 0:
               new_population.append(x)
        self.population = np.array(new_population)


    # Мутация через матожидание
    def rn(self, mu: float) -> float:
        r_n = random.normalvariate(mu, self.sigma)
        r = min(r_n, self.shape_graph[1]) if r_n > 0 else max(r_n, self.shape_graph[0])
        return r if random.random()>0.5 else random.uniform(*self.shape_graph[:2])


    # Заврнутая(для сброса среднего) функция юниформ
    def wrapper_uniform(self, mu: float = None) -> float:
        return random.uniform(*self.shape_graph[:2])


    # Скрестить гены и получить новый ген для ребенка
    def get_gen(self, parent: list[float], mutation_func: Callable, number_gen: int):
        return parent[number_gen] if random.random()>self.prob_mutation else mutation_func(parent[number_gen])


    # Получить детей от двух родителей
    def get_children(self, parent_1: list[float], parent_2: list[float], mutation_func: Callable):
        child_1 = [self.get_gen(parent_1, mutation_func, 0), self.get_gen(parent_2, mutation_func, 1)]
        child_2 = [self.get_gen(parent_2, mutation_func, 0), self.get_gen(parent_1, mutation_func, 1)]
        child_1.append(self.target_func(child_1))
        child_2.append(self.target_func(child_2))
        return child_1, child_2


    def animate_and_fit(self, i):
        selection_population = eval(f'{self.selection_func}(self.population)')
        np.random.shuffle(selection_population)
        new_population = deepcopy(selection_population)
        for i in range(self.len_selection//2):
            if self.choice_parent_type == "панксимия":
                child_1, child_2 = self.get_children(selection_population[i],
                                        selection_population[i+self.len_selection//2],
                                        self.mutation_func
                                        )
            else:
                list_dist = [math.dist(selection_population[i][:2], x[:2]) for x in selection_population[i+1:]]
                choice_func = np.argmax
                if self.choice_parent_type == "инбридинг": choice_func = np.argmin
                child_1, child_2 = self.get_children(selection_population[i],
                                            selection_population[choice_func(list_dist)],
                                            self.mutation_func
                                            )
            new_population.extend([child_1, child_2])

        self.population = np.array(new_population)

        # Перерисовка графика
        self.ax.cla()
        self.ax.plot_wireframe(self.X, self.Y, self.Z, rstride=10, cstride=10)
        self.ax.scatter(self.population[:,0], self.population[:,1], self.population[:,2],color='black')
        self.optim_point = min(self.population, key=self.target_func)
        return self.ax


    def fit(self, show = False, save_anim = False) -> None:
        self.create_population()

        # Выбор функции мутации
        self.mutation_func = self.wrapper_uniform if self.mutation_type == 'рандом' else self.rn

        # Выбор функции селекции
        self.selection_func = f'self.selection_{self.selection_types[self.selection_type]}'

        self.len_selection = int(len(self.population) / 2)
        # for _ in range(self.max_epoch):
        fig, self.ax = plt.subplots(
        1, 1, figsize=(8, 8), subplot_kw={'projection': '3d'})
        if self.X is None and self.Y is None:
            self.X, self.Y = np.meshgrid(np.arange(*self.shape_graph), np.arange(*self.shape_graph))
            self.Z = self.target_func([self.X, self.Y])

        self.ax.plot_wireframe(self.X, self.Y, self.Z, rstride=10, cstride=10)
        ani = FuncAnimation(fig, self.animate_and_fit, frames=self.max_epoch, blit=True)

        # saving to m4 using ffmpeg writer
        if save_anim:
            writervideo = FFMpegWriter(fps=5)
            ani.save("./test.mp4", writer=writervideo)
        return ani

In [4]:
%matplotlib inline
genom_test = Genom2000(max_epoch=20, selection_type="рулетки", mutation_type='не рандом', shape_graph=(-150, 150, 1))
print(genom_test)

%matplotlib notebook
anim = genom_test.fit(show = False)
# print(genom_test.optim_point)
HTML(anim.to_jshtml())

Genom2000(population_size=100, target_func=<function my_func at 0x000001D31A248680>, shape_graph=(-150, 150, 1), max_epoch=20, prob_mutation=0.05, selection_type='рулетки', mutation_type='не рандом', sigma=5, a=1.5, choice_parent_type='панксимия', optim_point=None, X=None, Y=None, Z=None, selection_types=defaultdict(<function Genom2000.<lambda>.<locals>.<lambda> at 0x000001D31A248B80>, {'турнир': 'a', 'рулетки': 'b', 'ранжирования': 'c', 'равномерное ранжирования': 'd'}))


<IPython.core.display.Javascript object>

In [5]:
default_dict = defaultdict(lambda: "None",{"a":1,"b":{"c":3}})

default_dict['dd']

'None'

In [6]:
print(genom_test.optim_point)

[-1.50000000e+02 -1.46084958e+02  6.63405585e-03]
